# Liners age analysis

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
from datetime import timedelta
import re
from dateutil.parser import parse
import string
import warnings
warnings.filterwarnings('ignore')
import plotly.graph_objects as go
import missingno as msno
from plotly.subplots import make_subplots
from sklearn.preprocessing import MinMaxScaler
import scipy
import researchpy as rp
from matplotlib.offsetbox import AnchoredText
import pacmap
from sklearn.compose import ColumnTransformer
from sklearn.cluster import KMeans
from sklearn.pipeline import Pipeline
import plotly.express as px
sns.set_style("darkgrid")
pd.set_option('display.max_columns', None)
pd.options.display.max_colwidth = 100

In [2]:
# read
tags=pd.read_excel("../../data/meta data/tags relevantes.xlsx")
tags_cc=tags.tag.to_list()
dic={}
for i,j in zip(tags.tag,tags.description):
    dic[i]=j

### 2. Data Loading

In [3]:
campañas=pd.read_csv("../../data/meta data/campaign_17December2022.csv")
campañas["Fechas"]=campañas["Fechas"]+' 00:00:00'
campañas.Fechas=pd.to_datetime(campañas.Fechas)

In [4]:
# Se lee csv
liners_age=pd.read_csv('../../data/consolidated data/liners_age_17December2022.csv', parse_dates=['Timestamp'], index_col='Timestamp')

In [5]:
# Se lee csv
df=pd.read_csv('../../data/consolidated data/cleaned_15December2022.csv', parse_dates=['Timestamp'], index_col='Timestamp')
df.sort_index(inplace=True)
df.rename(columns=dic,inplace=True)
df=df[tags.description.to_list()].drop(columns=["sag mill expert system"])

In [6]:
# Función que filtra tags por alta correlación
def corrkill(dataframe, features, corr_cut=0.4):

    df = dataframe[features]
    dfcorr = pd.DataFrame(np.triu(df.corr()), columns=df.columns, index=df.columns)
    dfcorr = dfcorr.stack().reset_index()
    dfcorr.columns = ['Feat1','Feat2','Val']
    dfcorr = dfcorr[~dfcorr['Val'].isin([0,1])]
    dfcorr = dfcorr[dfcorr['Val'].abs()>corr_cut]
    #dfcorr["Val"]=dfcorr["Val"].abs()
    
    return list(dfcorr['Feat2']), dfcorr.sort_values(by="Val",ascending=False)

# Merge

In [7]:
df_cleaned_age=df.join(liners_age).dropna().drop(columns=["crusher index","ball work index"])[['granulometry', 'charge cell',
       'sag power index', 'TPH', 'HH TPH', 'LL charge cell',
       'HH charge cell', 'speed', 
       'solid percentage', 'water',
       "Edad"]]
df_cleaned_age["dif_TPH_HH"]=df_cleaned_age["HH TPH"]-df_cleaned_age["TPH"]
df_cleaned_age["dif_CC_HH"]=df_cleaned_age["HH charge cell"]-df_cleaned_age["charge cell"]
df_cleaned_age["dif_CC_LL"]=df_cleaned_age["charge cell"]-df_cleaned_age["LL charge cell"]

In [8]:
pd.options.plotting.backend = "plotly"
fig=df_cleaned_age["dif_TPH_HH"].sample(10000).plot(kind='hist')
fig.update_layout(height=500, width=1200,title="Distribución delta TPH y HH TPH",) 
fig.show()

In [9]:
pd.options.plotting.backend = "plotly"
fig=df_cleaned_age["dif_CC_HH"].sample(10000).plot(kind='hist')
fig.update_layout(height=500, width=1200,title="Distribución delta CC y HH CC",) 
fig.show()

In [10]:
pd.options.plotting.backend = "plotly"
fig=df_cleaned_age["dif_CC_LL"].sample(10000).plot(kind='hist')
fig.update_layout(height=500, width=1200,title="Distribución delta CC y LL CC",) 
fig.show()

# Clusters

In [11]:
df_sample=df_cleaned_age.sample(5000)[["granulometry","sag power index"]]
fig = px.scatter(df_sample, x="granulometry", y="sag power index")

fig.update_layout(
    title="granulometría vs SPI",

height=500, width=1200
)  
fig.show()

In [12]:
# Cols
MinMax=MinMaxScaler()

# Selección de features a estandarizar (todas)

preprocessing_transformer = ColumnTransformer(transformers=[('MinMax', MinMax,  [i for i in df_sample.columns])])

# Iteración de inercias sobre cada número de clusters ejecutado
inertias = [
    [i, Pipeline([('Preprocessing', preprocessing_transformer),('k-means', KMeans(n_clusters=i, random_state=0))]).fit(df_sample)[1].inertia_]
    for i in range(1, 10)]

# Se guardan inercias y número de clusters en un data frame
inertias = pd.DataFrame(inertias, columns=["n° clusters", "inertia"])

# Visualización del método del codo
fig=px.line(inertias, x="n° clusters", y="inertia", title="Método del Codo con K-Means")
fig.update_layout(height=500, width=1200)
fig.show()

In [13]:
# Pipeline entrenamiento k-means con 6 clusters
pipeline1=Pipeline([('Preprocessing', preprocessing_transformer),('k-means', KMeans(n_clusters=3, random_state=0))])
# Entrenamiento de pipeline
pipeline1.fit(df_sample)

# Predicción de labels
labels=pipeline1.predict(df_sample)

# Para la visualización agregamos los labels al dataframe de baja dimensionalidad
df_sample["cluster"]=labels
df_sample.sort_values(by="cluster",inplace=True)
df_sample["cluster"]=df_sample["cluster"].astype("category")

In [14]:
fig = px.scatter(df_sample, x="granulometry", y="sag power index",color="cluster")

fig.update_layout(
    title="granulometría vs SPI",

height=500, width=1200
)  
fig.show()

In [15]:
# fit
pipeline1.fit(df_cleaned_age[["granulometry","sag power index"]])
# Predicción de labels
labels=pipeline1.predict(df_cleaned_age)
df_cleaned_age["cluster"]=labels

In [16]:
# Se obtienen tags altamente correlacionados y matriz que permite visualizar cuales son los par de tags altamente correlacionados
collinearity, table_cor=corrkill(df_cleaned_age,df_cleaned_age.columns)
table_cor

Feat1           Feat2       Val
81     LL charge cell  HH charge cell  0.999985
20        charge cell  LL charge cell  0.884543
21        charge cell  HH charge cell  0.884527
49                TPH          HH TPH  0.702817
114             speed           water  0.597326
28        charge cell       dif_CC_LL  0.480696
44    sag power index         cluster -0.470868
131  solid percentage      dif_TPH_HH -0.476796
27        charge cell       dif_CC_HH -0.480527
25        charge cell            Edad -0.597587
14       granulometry         cluster -0.597978
100    HH charge cell            Edad -0.665459
85     LL charge cell            Edad -0.665501
56                TPH      dif_TPH_HH -0.709562
129  solid percentage           water -0.768538
193         dif_CC_HH       dif_CC_LL -0.999946

In [17]:
# Tags altamente correlacionados
table_cor[(table_cor.Feat1=="speed") | (table_cor.Feat2=="speed")]

Feat1  Feat2       Val
114  speed  water  0.597326

In [18]:
# Tags altamente correlacionados
table_cor[(table_cor.Feat1=="solid percentage") | (table_cor.Feat2=="solid percentage")]

Feat1       Feat2       Val
131  solid percentage  dif_TPH_HH -0.476796
129  solid percentage       water -0.768538

In [19]:
# Categoria edad cluster
df_cleaned_age["Edad-cluster"]=df_cleaned_age["Edad"].astype(int).astype(str)+df_cleaned_age["cluster"].astype(str)

In [20]:
df_cleaned_age[["granulometry","sag power index"]].describe().apply(lambda x: round(x,2)).drop(index=["count"])

granulometry  sag power index
mean         59.59           114.62
std          12.19            24.05
min          22.09            40.20
25%          51.42            97.48
50%          61.62           111.52
75%          66.49           126.00
max          96.42           188.58

In [21]:
df_cleaned_age[["granulometry","sag power index","cluster"]].groupby("cluster").mean().apply(lambda x: round(x,2))#.sort_values(by="granulometry")

granulometry  sag power index
cluster                               
0               63.48           151.99
1               67.89           100.95
2               46.85           111.84

### Caracteristica de clusters.
* cluster 0: F80 medio y SPI alto.
* cluster 1:F80 alto y SPI bajo.
* cluster 2: F80 bajo y SPI medio.

In [22]:
dic_cluster={0:"Material de tamaño medio y alta dureza",1:"Material de tamaño pequeño y baja dureza",2:"Material de tamaño grande y dureza media"}
dic_edad={0:"Revestimientos nuevos",1:"Revestimientos con desgaste medio",2:"Revestimientos desgastados"}

In [23]:
df_cleaned_age["Descripción"]=df_cleaned_age["Edad"].replace(dic_edad)+', '+df_cleaned_age["cluster"].replace(dic_cluster)

In [24]:
df_cleaned_age.Edad=df_cleaned_age.Edad.astype(int)
df_cleaned_age.Edad=df_cleaned_age.Edad.replace(dic_edad)

In [25]:
df_cleaned_age.cluster=df_cleaned_age.cluster.astype(int)
df_cleaned_age.cluster=df_cleaned_age.cluster.replace(dic_cluster)

# Análisis Edad

In [26]:
descrip_age=df_cleaned_age.groupby("Edad").mean()[['charge cell', 'TPH', 'HH TPH', 'LL charge cell',
       'HH charge cell', 'speed', 
       'solid percentage', 'water',
        'dif_TPH_HH', 'dif_CC_HH', 'dif_CC_LL',]]
descrip_age.index=pd.Series(descrip_age.index).replace(dic_edad)
descrip_age.apply(lambda x: round(x,2))

charge cell      TPH   HH TPH  \
Edad                                                               
Revestimientos con desgaste medio       807.54  3949.23  4125.06   
Revestimientos desgastados              729.99  4164.01  4295.96   
Revestimientos nuevos                   831.85  3981.67  4134.73   

                                   LL charge cell  HH charge cell  speed  \
Edad                                                                       
Revestimientos con desgaste medio          776.14          856.14   8.89   
Revestimientos desgastados                 702.78          782.78   8.69   
Revestimientos nuevos                      802.39          882.39   8.75   

                                   solid percentage    water  dif_TPH_HH  \
Edad                                                                       
Revestimientos con desgaste medio             72.57  1480.36      175.83   
Revestimientos desgastados                    73.23  1513.87      131.96   
Revestimientos nuevos                         72.58  1498.82      153.07   

                                   dif_CC_HH  dif_CC_LL  
Edad                                                     
Revestimientos con desgaste medio      48.60      31.40  
Revestimientos desgastados             52.80      27.20  
Revestimientos nuevos                  50.54      29.46

In [27]:
df_sample=df_cleaned_age.sample(10000).replace({j:i for i,j in zip(dic_edad.keys(),dic_edad.values())}).sort_values(by="Edad",ascending=True).replace(dic_edad)

In [28]:
fig = px.box(df_sample, y="HH TPH", color="Edad")
fig.update_layout(
height=500, width=1200,title="Box plot HH TPH",
)  
fig.show()

In [29]:
fig = px.box(df_sample, y="HH charge cell", color="Edad")
fig.update_layout(
height=500, width=1200,title="Box plot HH charge cell",
)  
fig.show()

In [30]:
fig = px.box(df_sample, y="TPH", color="Edad")
fig.update_layout(
height=500, width=1200,title="Box plot TPH",
)  
fig.show()

In [31]:
fig = px.box(df_sample, y="charge cell", color="Edad")
fig.update_layout(
height=500, width=1200,title="Box plot charge cell",
)  
fig.show()

# Análisis Cluster

In [32]:
descrip_cluster=df_cleaned_age.groupby("cluster").mean()[['charge cell', 'TPH', 'HH TPH', 'LL charge cell',
       'HH charge cell', 'speed', 
       'solid percentage', 'water',
        'dif_TPH_HH', 'dif_CC_HH', 'dif_CC_LL',]]
descrip_cluster.index=pd.Series(descrip_cluster.index).replace(dic_cluster)
descrip_cluster.apply(lambda x: round(x,2))

charge cell      TPH   HH TPH  \
cluster                                                                   
Material de tamaño grande y dureza media       788.92  4010.14  4204.46   
Material de tamaño medio y alta dureza         800.05  3867.53  4094.15   
Material de tamaño pequeño y baja dureza       781.74  4123.84  4214.52   

                                          LL charge cell  HH charge cell  \
cluster                                                                    
Material de tamaño grande y dureza media          750.51          830.52   
Material de tamaño medio y alta dureza            771.74          851.74   
Material de tamaño pequeño y baja dureza          759.05          839.05   

                                          speed  solid percentage    water  \
cluster                                                                      
Material de tamaño grande y dureza media   8.90             71.53  1578.74   
Material de tamaño medio y alta dureza     8.94             71.35  1541.31   
Material de tamaño pequeño y baja dureza   8.61             74.42  1415.88   

                                          dif_TPH_HH  dif_CC_HH  dif_CC_LL  
cluster                                                                     
Material de tamaño grande y dureza media      194.32      41.60      38.40  
Material de tamaño medio y alta dureza        226.62      51.69      28.31  
Material de tamaño pequeño y baja dureza       90.68      57.30      22.70

In [33]:
df_sample=df_cleaned_age.sample(10000)

In [34]:
fig = px.box(df_sample, y="HH TPH", color="cluster")
fig.update_layout(
height=500, width=1200,title="Box plot HH TPH",
)  
fig.show()

In [35]:
fig = px.box(df_sample, y="HH charge cell", color="cluster")
fig.update_layout(
height=500, width=1200,title="Box plot HH charge cell",
)  
fig.show()

In [36]:
fig = px.box(df_sample, y="water", color="cluster")
fig.update_layout(
height=500, width=1200,title="Box plot water",
)  
fig.show()

In [37]:
fig = px.box(df_sample, y="speed", color="cluster")
fig.update_layout(
height=500, width=1200,title="Box plot speed",
)  
fig.show()

In [38]:
fig = px.box(df_sample, y="TPH", color="cluster")
fig.update_layout(
height=500, width=1200,title="Box plot TPH",
)  
fig.show()

In [39]:
fig = px.box(df_sample, y="dif_TPH_HH", color="cluster")
fig.update_layout(
height=500, width=1200,title="Box plot Caidas de TPH",
)  
fig.show()

# Análisis Edad - Cluster

In [40]:
tags_interes=["Edad","cluster",'charge cell',
        'TPH', 'HH TPH', 'LL charge cell',
       'HH charge cell', 'speed', 
       'solid percentage', 'water',
        'dif_TPH_HH', 'dif_CC_HH', 'dif_CC_LL', 
       ]

In [41]:
df_cleaned_age.Edad=df_cleaned_age.Edad.replace({j:i for i,j in zip(dic_edad.keys(),dic_edad.values())})
df_cleaned_age.cluster=df_cleaned_age.cluster.replace({j:i for i,j in zip(dic_cluster.keys(),dic_cluster.values())})

In [42]:
descrip=df_cleaned_age.groupby("Edad-cluster").mean()[tags_interes].apply(lambda x: round(x,2))

In [43]:
descrip["Descripción"]=descrip["Edad"].replace(dic_edad)+', '+descrip["cluster"].replace(dic_cluster)

In [44]:
descrip

Edad  cluster  charge cell      TPH   HH TPH  LL charge cell  \
Edad-cluster                                                                 
00             0.0      0.0       844.28  3811.66  4041.87          814.48   
01             0.0      1.0       824.36  4061.78  4161.47          801.28   
02             0.0      2.0       835.16  3972.09  4156.82          795.69   
10             1.0      0.0       799.70  3828.53  4086.19          767.95   
11             1.0      1.0       805.75  4084.14  4188.63          781.67   
12             1.0      2.0       814.64  3870.82  4076.52          775.01   
20             2.0      0.0       741.64  4006.00  4176.90          720.98   
21             2.0      1.0       721.97  4215.04  4285.43          700.83   
22             2.0      2.0       735.33  4159.24  4349.82          698.73   

              HH charge cell  speed  solid percentage    water  dif_TPH_HH  \
Edad-cluster                                                                 
00                    894.48   8.94             70.35  1600.62      230.21   
01                    881.28   8.62             74.04  1428.95       99.69   
02                    875.71   8.82             71.80  1539.67      184.73   
10                    847.94   9.01             71.46  1511.37      257.66   
11                    861.67   8.74             74.31  1403.16      104.49   
12                    855.01   9.00             71.27  1549.72      205.70   
20                    800.98   8.84             72.52  1511.34      170.90   
21                    780.83   8.49             74.85  1415.16       70.38   
22                    778.73   8.86             71.58  1630.47      190.58   

              dif_CC_HH  dif_CC_LL  \
Edad-cluster                         
00                50.20      29.80   
01                56.92      23.08   
02                40.54      39.47   
10                48.24      31.76   
11                55.92      24.08   
12                40.37      39.64   
20                59.35      20.66   
21                58.87      21.13   
22                43.40      36.60   

                                                                              Descripción  
Edad-cluster                                                                               
00                          Revestimientos nuevos, Material de tamaño medio y alta dureza  
01                        Revestimientos nuevos, Material de tamaño pequeño y baja dureza  
02                        Revestimientos nuevos, Material de tamaño grande y dureza media  
10              Revestimientos con desgaste medio, Material de tamaño medio y alta dureza  
11            Revestimientos con desgaste medio, Material de tamaño pequeño y baja dureza  
12            Revestimientos con desgaste medio, Material de tamaño grande y dureza media  
20                     Revestimientos desgastados, Material de tamaño medio y alta dureza  
21                   Revestimientos desgastados, Material de tamaño pequeño y baja dureza  
22                   Revestimientos desgastados, Material de tamaño grande y dureza media

In [45]:
df_cleaned_age.describe().apply(lambda x: round(x,2)).drop(index=["count"],columns=["cluster","Edad"])

granulometry  charge cell  sag power index      TPH   HH TPH  \
mean         59.59       787.80           114.62  4034.27  4187.81   
std          12.19        69.71            24.05   457.42   322.32   
min          22.09       549.23            40.20  2546.81  3139.58   
25%          51.42       744.18            97.48  3799.25  4000.00   
50%          61.62       788.78           111.52  4151.50  4250.00   
75%          66.49       834.69           126.00  4387.08  4450.00   
max          96.42       999.95           188.58  4799.63  4800.00   

      LL charge cell  HH charge cell  speed  solid percentage    water  \
mean          758.46          838.46   8.78             72.80  1497.71   
std            61.13           61.14   0.76              4.85   392.47   
min           580.00          660.00   0.64             62.00     0.00   
25%           720.00          800.00   8.52             68.05  1247.22   
50%           760.00          840.00   9.00             74.61  1397.80   
75%           800.00          880.00   9.25             77.08  1789.57   
max           930.46         1015.35   9.65             81.97  2668.88   

      dif_TPH_HH  dif_CC_HH  dif_CC_LL  
mean      153.54      50.66      29.34  
std       325.40      32.52      32.52  
min     -1459.38    -139.89    -366.95  
25%        -3.48      30.12      10.29  
50%        12.60      50.21      29.79  
75%       143.53      69.71      49.88  
max      2091.47     446.95     205.22

In [46]:
df_sample

granulometry  charge cell  sag power index          TPH  \
Timestamp                                                                      
2022-01-29 06:06:00     51.146423   915.406917       104.332200  4187.257309   
2021-12-07 03:44:00     64.083051   697.273245       100.417000  3981.306208   
2020-07-08 16:14:00     84.743813   787.657565        97.366800  3899.699976   
2022-04-10 03:46:00     47.008313   810.679966       107.000000  3321.986899   
2021-04-26 20:38:00     64.266173   792.180958       108.126900  3149.322123   
...                           ...          ...              ...          ...   
2021-11-17 04:27:00     76.713516   753.801488       100.501800  4245.268554   
2021-10-13 20:21:00     59.332703   828.133932       116.774195  4473.013598   
2020-06-07 09:22:00     48.942397   825.063102       143.000000  2911.870502   
2020-09-15 08:40:00     47.720156   788.030299       126.038800  4487.504266   
2020-12-23 01:59:00     81.761394   672.870355       115.832795  4310.592907   

                     HH TPH  LL charge cell  HH charge cell     speed  \
Timestamp                                                               
2022-01-29 06:06:00  4350.0           880.0           960.0  9.298400   
2021-12-07 03:44:00  4000.0           675.0           755.0  8.989119   
2020-07-08 16:14:00  3900.0           810.0           890.0  7.906403   
2022-04-10 03:46:00  3400.0           780.0           860.0  9.285086   
2021-04-26 20:38:00  3150.0           780.0           860.0  8.557824   
...                     ...             ...             ...       ...   
2021-11-17 04:27:00  4250.0           730.0           810.0  9.292465   
2021-10-13 20:21:00  4500.0           820.0           900.0  8.877572   
2020-06-07 09:22:00  4200.0           790.0           870.0  9.062583   
2020-09-15 08:40:00  4500.0           720.0           800.0  9.311741   
2020-12-23 01:59:00  4300.0           675.0           755.0  8.479462   

                     solid percentage        water  \
Timestamp                                            
2022-01-29 06:06:00         65.070571  2249.565161   
2021-12-07 03:44:00         77.928390  1126.139192   
2020-07-08 16:14:00         77.973875  1101.559003   
2022-04-10 03:46:00         65.060423  1784.958575   
2021-04-26 20:38:00         78.038458   885.844276   
...                               ...          ...   
2021-11-17 04:27:00         66.499055  2133.039474   
2021-10-13 20:21:00         76.526043  1370.539361   
2020-06-07 09:22:00         68.133256  1363.369343   
2020-09-15 08:40:00         67.386024  2175.144153   
2020-12-23 01:59:00         72.865652  1603.081468   

                                                  Edad   dif_TPH_HH  \
Timestamp                                                             
2022-01-29 06:06:00              Revestimientos nuevos   162.742691   
2021-12-07 03:44:00         Revestimientos desgastados    18.693792   
2020-07-08 16:14:00  Revestimientos con desgaste medio     0.300024   
2022-04-10 03:46:00  Revestimientos con desgaste medio    78.013101   
2021-04-26 20:38:00  Revestimientos con desgaste medio     0.677877   
...                                                ...          ...   
2021-11-17 04:27:00         Revestimientos desgastados     4.731446   
2021-10-13 20:21:00  Revestimientos con desgaste medio    26.986402   
2020-06-07 09:22:00              Revestimientos nuevos  1288.129498   
2020-09-15 08:40:00         Revestimientos desgastados    12.495734   
2020-12-23 01:59:00         Revestimientos desgastados   -10.592907   

                      dif_CC_HH  dif_CC_LL  \
Timestamp                                    
2022-01-29 06:06:00   44.593083  35.406917   
2021-12-07 03:44:00   57.726755  22.273245   
2020-07-08 16:14:00  102.342435 -22.342435   
2022-04-10 03:46:00   49.320034  30.679966   
2021-04-26 20:38:00   67.819042  12.180958   
...                         ...        ...   
2021-11-17 04:27:00   56.198512  23

In [47]:
df_sample=df_cleaned_age.sample(10000).sort_values(by="Edad-cluster")
for i in ['charge cell', 'TPH', 'HH TPH',
       'HH charge cell', 'speed', 
       'solid percentage', 'water',
        'dif_TPH_HH', 'dif_CC_HH',]:
       #print(i)
       fig = px.box(df_sample, y=f"{i}", color="Descripción")
       fig.update_layout(
       height=500, width=1200, title=f"Box plot {i}"
       )  
       fig.show()
       display(descrip.sort_index()[[i,"Descripción"]])
       print("")

charge cell  \
Edad-cluster                
00                 844.28   
01                 824.36   
02                 835.16   
10                 799.70   
11                 805.75   
12                 814.64   
20                 741.64   
21                 721.97   
22                 735.33   

                                                                              Descripción  
Edad-cluster                                                                               
00                          Revestimientos nuevos, Material de tamaño medio y alta dureza  
01                        Revestimientos nuevos, Material de tamaño pequeño y baja dureza  
02                        Revestimientos nuevos, Material de tamaño grande y dureza media  
10              Revestimientos con desgaste medio, Material de tamaño medio y alta dureza  
11            Revestimientos con desgaste medio, Material de tamaño pequeño y baja dureza  
12            Revestimientos con desgaste medio, Material de tamaño grande y dureza media  
20                     Revestimientos desgastados, Material de tamaño medio y alta dureza  
21                   Revestimientos desgastados, Material de tamaño pequeño y baja dureza  
22                   Revestimientos desgastados, Material de tamaño grande y dureza media

TPH  \
Edad-cluster            
00            3811.66   
01            4061.78   
02            3972.09   
10            3828.53   
11            4084.14   
12            3870.82   
20            4006.00   
21            4215.04   
22            4159.24   

                                                                              Descripción  
Edad-cluster                                                                               
00                          Revestimientos nuevos, Material de tamaño medio y alta dureza  
01                        Revestimientos nuevos, Material de tamaño pequeño y baja dureza  
02                        Revestimientos nuevos, Material de tamaño grande y dureza media  
10              Revestimientos con desgaste medio, Material de tamaño medio y alta dureza  
11            Revestimientos con desgaste medio, Material de tamaño pequeño y baja dureza  
12            Revestimientos con desgaste medio, Material de tamaño grande y dureza media  
20                     Revestimientos desgastados, Material de tamaño medio y alta dureza  
21                   Revestimientos desgastados, Material de tamaño pequeño y baja dureza  
22                   Revestimientos desgastados, Material de tamaño grande y dureza media

HH TPH  \
Edad-cluster            
00            4041.87   
01            4161.47   
02            4156.82   
10            4086.19   
11            4188.63   
12            4076.52   
20            4176.90   
21            4285.43   
22            4349.82   

                                                                              Descripción  
Edad-cluster                                                                               
00                          Revestimientos nuevos, Material de tamaño medio y alta dureza  
01                        Revestimientos nuevos, Material de tamaño pequeño y baja dureza  
02                        Revestimientos nuevos, Material de tamaño grande y dureza media  
10              Revestimientos con desgaste medio, Material de tamaño medio y alta dureza  
11            Revestimientos con desgaste medio, Material de tamaño pequeño y baja dureza  
12            Revestimientos con desgaste medio, Material de tamaño grande y dureza media  
20                     Revestimientos desgastados, Material de tamaño medio y alta dureza  
21                   Revestimientos desgastados, Material de tamaño pequeño y baja dureza  
22                   Revestimientos desgastados, Material de tamaño grande y dureza media

HH charge cell  \
Edad-cluster                   
00                    894.48   
01                    881.28   
02                    875.71   
10                    847.94   
11                    861.67   
12                    855.01   
20                    800.98   
21                    780.83   
22                    778.73   

                                                                              Descripción  
Edad-cluster                                                                               
00                          Revestimientos nuevos, Material de tamaño medio y alta dureza  
01                        Revestimientos nuevos, Material de tamaño pequeño y baja dureza  
02                        Revestimientos nuevos, Material de tamaño grande y dureza media  
10              Revestimientos con desgaste medio, Material de tamaño medio y alta dureza  
11            Revestimientos con desgaste medio, Material de tamaño pequeño y baja dureza  
12            Revestimientos con desgaste medio, Material de tamaño grande y dureza media  
20                     Revestimientos desgastados, Material de tamaño medio y alta dureza  
21                   Revestimientos desgastados, Material de tamaño pequeño y baja dureza  
22                   Revestimientos desgastados, Material de tamaño grande y dureza media

speed  \
Edad-cluster          
00             8.94   
01             8.62   
02             8.82   
10             9.01   
11             8.74   
12             9.00   
20             8.84   
21             8.49   
22             8.86   

                                                                              Descripción  
Edad-cluster                                                                               
00                          Revestimientos nuevos, Material de tamaño medio y alta dureza  
01                        Revestimientos nuevos, Material de tamaño pequeño y baja dureza  
02                        Revestimientos nuevos, Material de tamaño grande y dureza media  
10              Revestimientos con desgaste medio, Material de tamaño medio y alta dureza  
11            Revestimientos con desgaste medio, Material de tamaño pequeño y baja dureza  
12            Revestimientos con desgaste medio, Material de tamaño grande y dureza media  
20                     Revestimientos desgastados, Material de tamaño medio y alta dureza  
21                   Revestimientos desgastados, Material de tamaño pequeño y baja dureza  
22                   Revestimientos desgastados, Material de tamaño grande y dureza media

solid percentage  \
Edad-cluster                     
00                       70.35   
01                       74.04   
02                       71.80   
10                       71.46   
11                       74.31   
12                       71.27   
20                       72.52   
21                       74.85   
22                       71.58   

                                                                              Descripción  
Edad-cluster                                                                               
00                          Revestimientos nuevos, Material de tamaño medio y alta dureza  
01                        Revestimientos nuevos, Material de tamaño pequeño y baja dureza  
02                        Revestimientos nuevos, Material de tamaño grande y dureza media  
10              Revestimientos con desgaste medio, Material de tamaño medio y alta dureza  
11            Revestimientos con desgaste medio, Material de tamaño pequeño y baja dureza  
12            Revestimientos con desgaste medio, Material de tamaño grande y dureza media  
20                     Revestimientos desgastados, Material de tamaño medio y alta dureza  
21                   Revestimientos desgastados, Material de tamaño pequeño y baja dureza  
22                   Revestimientos desgastados, Material de tamaño grande y dureza media

water  \
Edad-cluster            
00            1600.62   
01            1428.95   
02            1539.67   
10            1511.37   
11            1403.16   
12            1549.72   
20            1511.34   
21            1415.16   
22            1630.47   

                                                                              Descripción  
Edad-cluster                                                                               
00                          Revestimientos nuevos, Material de tamaño medio y alta dureza  
01                        Revestimientos nuevos, Material de tamaño pequeño y baja dureza  
02                        Revestimientos nuevos, Material de tamaño grande y dureza media  
10              Revestimientos con desgaste medio, Material de tamaño medio y alta dureza  
11            Revestimientos con desgaste medio, Material de tamaño pequeño y baja dureza  
12            Revestimientos con desgaste medio, Material de tamaño grande y dureza media  
20                     Revestimientos desgastados, Material de tamaño medio y alta dureza  
21                   Revestimientos desgastados, Material de tamaño pequeño y baja dureza  
22                   Revestimientos desgastados, Material de tamaño grande y dureza media

dif_TPH_HH  \
Edad-cluster               
00                230.21   
01                 99.69   
02                184.73   
10                257.66   
11                104.49   
12                205.70   
20                170.90   
21                 70.38   
22                190.58   

                                                                              Descripción  
Edad-cluster                                                                               
00                          Revestimientos nuevos, Material de tamaño medio y alta dureza  
01                        Revestimientos nuevos, Material de tamaño pequeño y baja dureza  
02                        Revestimientos nuevos, Material de tamaño grande y dureza media  
10              Revestimientos con desgaste medio, Material de tamaño medio y alta dureza  
11            Revestimientos con desgaste medio, Material de tamaño pequeño y baja dureza  
12            Revestimientos con desgaste medio, Material de tamaño grande y dureza media  
20                     Revestimientos desgastados, Material de tamaño medio y alta dureza  
21                   Revestimientos desgastados, Material de tamaño pequeño y baja dureza  
22                   Revestimientos desgastados, Material de tamaño grande y dureza media

dif_CC_HH  \
Edad-cluster              
00                50.20   
01                56.92   
02                40.54   
10                48.24   
11                55.92   
12                40.37   
20                59.35   
21                58.87   
22                43.40   

                                                                              Descripción  
Edad-cluster                                                                               
00                          Revestimientos nuevos, Material de tamaño medio y alta dureza  
01                        Revestimientos nuevos, Material de tamaño pequeño y baja dureza  
02                        Revestimientos nuevos, Material de tamaño grande y dureza media  
10              Revestimientos con desgaste medio, Material de tamaño medio y alta dureza  
11            Revestimientos con desgaste medio, Material de tamaño pequeño y baja dureza  
12            Revestimientos con desgaste medio, Material de tamaño grande y dureza media  
20                     Revestimientos desgastados, Material de tamaño medio y alta dureza  
21                   Revestimientos desgastados, Material de tamaño pequeño y baja dureza  
22                   Revestimientos desgastados, Material de tamaño grande y dureza media

In [62]:
# fit
#df_cleaned_age["cluster spi"]= KMeans(n_clusters=4, random_state=0).fit_predict(df_cleaned_age[["sag power index"]])
#fig = px.box(df_cleaned_age.sample(10000), y="sag power index", color="cluster spi")
#fig.update_layout(
#height=500, width=1200
#)  
#fig.show()